# Panel dashboard with binned-merged data
10/26/2019

## TO-DOs
- Load `sensorinventory_df.parq` and use it in summary displays (tables, text) of each TROCAS
- Add a colorbar legend/label
- Problems I was seeing with chlorophyll, isotopes, etc, all apparently had to do with **negative values with a log scale** (logz=True)! I'll need to implement log scaling as an option (checkbox), that maybe is only available for a pre-defined set of parameters.
- Add global min-max range to each parameter. Then add capability to plot using global, fixed min-max, while also allowing a floating, self-scalable range (what's currently happening by default)
- Overhaul histogram so it truly responds dynamically to all selections.
  - The histogram is responding dynamically to changes in TROCAS number (but with hiccups!), but not to changes in variables that lead to a completely different value range -- both x axis and y axis ranges. The xlabel does update, but the axis range doesn't. For now, updating the histogram requires rerunning the cell. See https://holoviz.org/tutorial/Interlinked_Plots.html for good examples of a linked histogram plots, but using a more complex scheme (streams, `from holoviews.streams import Selection1D`, etc). See also http://earthml.pyviz.org/topics/Carbon_Flux.html
  - This scheme didn't work. It still required rerunning the code to get the xaxis range to update
    ```python
       obs_param_dynmap_ser = geopoints.dframe()[geopoints.dimensions(selection='value')[0].name]
       bin_range=(obs_param_dynmap_ser.min(), obs_param_dynmap_ser.max()) # using this bin_range in hist()
     ```

## Notes

### Setting color range limits
Use `clim` option (or hvplot) parameter, eg: `clim=(5000, 8000)`

### Setting colormap min, max and NaN colors
Use the `clipping_colors` option, like this:
```python
clipping = {'min': 'red', 'max': 'green', 'NaN': 'transparent'}
myplot.opts(clipping_colors=clipping)
```

### Running this notebook as a stand-alone panel

Panel can be launched directly from here by running this statement:
```bash
! panel serve --show --port 5009 map_dashboard_clean.ipynb
```
But it's better to run it from the shell. Use the same command, except for the `!`.

The port number is chosen by the user, but it looks like it's conventional to choose one in the 5001-5009 range.

In [1]:
from collections import OrderedDict as odict
from pathlib import Path
import numpy as np
import pandas as pd
import geopandas as gpd

import colorcet as cc, param as pm, holoviews as hv, panel as pn, datashader as ds
import geoviews as gv
import geoviews.tile_sources as gts
from holoviews.operation.datashader import rasterize, shade, spread
import hvplot.pandas  # noqa

hv.extension('bokeh', logo=False)
pn.extension(logo=False)

/home/mayorga/miniconda/envs/holoviztrocas_panelapp/lib/python3.7/site-packages/datashader/transfer_functions.py:21: FutureWarning: xarray subclass Image should explicitly define __slots__
  class Image(xr.DataArray):


In [2]:
trocas_dpth = './data'

# Load and pre-process Binned-Merged data

In [3]:
mbdata_df = pd.read_parquet(Path(trocas_dpth) / 'merged_1minbinned_df.parq', engine='fastparquet')

In [4]:
mbdata_df.columns

Index(['date_time', 'TROCAS_nbr', 'TROCAS_nbr_lico', 'TROCAS_nbr_gps',
       'longitude', 'latitude', 'collectiontype_lico', 'filename_lico',
       'reldirpath_lico', 'CO2(ppm)', 'TROCAS_nbr_sond', 'collectiontype_sond',
       'filename_sond', 'reldirpath_sond', 'ODO mg/L', 'pH', 'Temp °C',
       'Turbidity FNU', 'Chlorophyll µg/L', 'TROCAS_nbr_pica', '12CO2',
       'Delta_Raw_iCO2', '12CH4', 'Delta_iCH4_Raw'],
      dtype='object')

In [5]:
mbdata_df = mbdata_df[mbdata_df.latitude.notnull()]

In [6]:
len(mbdata_df)

45885

In [7]:
# Store into new variables b/c the original ones will be overwritten into web mercator
mbdata_df['latdeg'] = mbdata_df['latitude']
mbdata_df['londeg'] = mbdata_df['longitude']

In [8]:
mbdata_points = gv.Points(mbdata_df, kdims=['longitude', 'latitude']) #, vdims=['date_time'])
mbdata_points = gv.Dataset(gv.operation.project_points(mbdata_points))

# Diel stations

## Extract diel file flags (collectiontype) and create points, by individual files via groupby

In [9]:
mbdata_dielcoll_df = mbdata_df[(mbdata_df.collectiontype_lico == 'diel') | (mbdata_df.collectiontype_sond == 'diel')]

In [10]:
# 'date_time':'mean',
agg_dct = odict(
    TROCAS_nbr=('TROCAS_nbr', 'first'), 
    collectiontype_lico=('collectiontype_lico', 'first'), 
    collectiontype_sond=('collectiontype_sond', 'first'), 
    longitude=('longitude', 'mean'),
    latitude=('latitude', 'mean'),
    bin_count=('date_time', 'count')
)

- Add min & max (or 1 stdev) to longitude and latitude agg, to help assess what's being averaged, whether it really is a tightly clustered set of points. But will then need to use the scheme to simplify multi-level columns to single-level column names (eg, longitude_min, longitude_mean)
- Including `date_time` in agg_dct results in an error. Investigate it.

In [11]:
mbdata_dielcoll_pts_df = mbdata_dielcoll_df.groupby(['filename_lico', 'filename_sond']).agg(**agg_dct)
mbdata_dielcoll_pts_df.reset_index(inplace=True)

In [12]:
mbdata_dielcoll_points = gv.Points(mbdata_dielcoll_pts_df, kdims=['longitude', 'latitude'],
                                  label='stations - diel files')
mbdata_dielcoll_points = gv.operation.project_points(mbdata_dielcoll_points)

## "Jeff's" stations

In [13]:
stations_gdf = gpd.read_file(Path(trocas_dpth) / 'stations.geojson')

In [14]:
stations_gv_vdims = gv.Points(stations_gdf, vdims=['name'], label="stations - jeff's set")

# Plots and Maps

In [15]:
esri_wtm_tiles = ('http://services.arcgisonline.com/arcgis/rest/services/'
                  'World_Topo_Map/MapServer/MapServer/tile/{Z}/{Y}/{X}')

In [16]:
# geo_bg = gts.EsriImagery.options(alpha=0.6, bgcolor="black")
# basemap = bases['EsriTerrain']
basemap = gts.WMTS(esri_wtm_tiles)

In [17]:
# SPREAD background points
rasterized_postds2 = rasterize(mbdata_points, aggregator=ds.count())
# These options are not making any obvious difference: .opts(logz=True, cmap=list(reversed(colorcet.gray)))
# hv.DynamicMap(points) instead of selected?
shaded_postds2 = shade(rasterized_postds2, cmap=list(reversed(cc.b_linear_grey_10_95_c0)))
spreaded_postds = spread(shaded_postds2, px=1)

## Select a TROCAS and a variable

Dependent selectors below are based on [this post](https://stackoverflow.com/questions/57870870/how-do-i-automatically-update-a-dropdown-selection-widget-when-another-selection)

In [18]:
# Add global min-max values to this data structure
_obs_parameters = {
    'Licor': ['CO2(ppm)'],
    'EXOSonde': ['Temp °C', 'ODO mg/L', 'pH', 'Turbidity FNU', 'Chlorophyll µg/L'],
    'Picarro': ['12CO2', 'Delta_Raw_iCO2', '12CH4', 'Delta_iCH4_Raw']
}

sensor = pn.widgets.Select(
    name='Sensor',
    value='Licor', 
    options=list(_obs_parameters.keys())
)

obs_parameter = pn.widgets.Select(
    name='Parameter',
    value=_obs_parameters[sensor.value][0], 
    options=_obs_parameters[sensor.value]
)

@pn.depends(sensor.param.value, watch=True)
def _update_obs_parameters(sensor):
    obs_parameter.value = _obs_parameters[sensor][0]
    obs_parameter.options = _obs_parameters[sensor]

In [19]:
trocas_nbr = pn.widgets.Select(
    name='TROCAS Number',
    value='6', 
    options=[str(i) for i in range(1, 7)]
)

In [20]:
# I'm not getting this to work with logz=use_logscale.param.value or logz=use_logscale.value
# use_logscale = pn.widgets.Checkbox(name='Use Log scale', value=False)

## Map plot

In [21]:
# selected = mbdata_points.select(TROCAS_nbr=trocas_nbr.value)
# geopoints = selected.to(gv.Points, ['longitude', 'latitude'], [obs_parameter.value], []
#                         ).opts(**geo_opts)

# geopoints.opts(clim=obs_variable_clim)
# colorbar_opts={'title': 'my parameter (units)'},
#        title works but its position at the top is of limited use; label is not accepted
# clabel works as a stand-alone opts parameter, but has the same effect as title

In [22]:
size_opts = dict(width=800, height=600)
geo_opts = dict(global_extent=False, cmap=cc.fire, colorbar=True)  # logz=True, 

In [23]:
def mbdata_points_tr(ds, obs_param, TROCAS_nbr=None):
    selected = ds if TROCAS_nbr is None else ds.select(TROCAS_nbr=TROCAS_nbr)
    return selected.to(gv.Points, ['longitude', 'latitude'], [obs_param, 'date_time'], [])

geopoints = mbdata_points.apply(
    mbdata_points_tr, 
    obs_param=obs_parameter.param.value,
    TROCAS_nbr=trocas_nbr.param.value
).opts(**geo_opts)

geopoints_alltr = mbdata_points.apply(
    mbdata_points_tr, 
    obs_param=obs_parameter.param.value,
    TROCAS_nbr=None
).opts(**geo_opts)

In [24]:
print(geopoints)

:DynamicMap   []


In [25]:
# xlabel and ylabel: can't find a way to actually turn them off
mainmap = (
    basemap * spreaded_postds
    * geopoints.apply.opts(color=obs_parameter.param.value,
                           size=3, clipping_colors={'NaN':'transparent'})
    * stations_gv_vdims.opts(color='green', size=20, marker='diamond', show_legend=True, tools=['hover'])
    * mbdata_dielcoll_points.opts(color='blue', size=6, marker='square', show_legend=True, tools=['hover'])
).opts(**size_opts, toolbar='above', legend_position='top_left', xlabel='', ylabel='')

In [26]:
# bin_range=(xmin, xmax)
hist = geopoints.hist(adjoin=False)
hist_alltr = geopoints_alltr.hist(adjoin=False).opts(color='gray')

In [27]:
pn.Column(
    pn.Row(trocas_nbr, sensor, obs_parameter),
    (hist_alltr * hist).opts(width=800, height=200, toolbar=None),
    mainmap
).servable()

Column
    [0] Row
        [0] Select(name='TROCAS Number', options=['1', '2', '3', ...], value='6')
        [1] Select(name='Sensor', options=['Licor', 'EXOSonde', ...], value='Licor')
        [2] Select(name='Parameter', options=['CO2(ppm)'], value='CO2(ppm)')
    [1] HoloViews(DynamicMap)
    [2] HoloViews(DynamicMap)

#### For colorbar attributes:

AttributeError [Call holoviews.ipython.show_traceback() for details]

unexpected attribute 'clabel' to ColorBar, possible attributes are background_fill_alpha, background_fill_color, bar_line_alpha, bar_line_cap, bar_line_color, bar_line_dash, bar_line_dash_offset, bar_line_join, bar_line_width, border_line_alpha, border_line_cap, border_line_color, border_line_dash, border_line_dash_offset, border_line_join, border_line_width, color_mapper, formatter, height, js_event_callbacks, js_property_callbacks, label_standoff, level, location, major_label_overrides, major_label_text_align, major_label_text_alpha, major_label_text_baseline, major_label_text_color, major_label_text_font, major_label_text_font_size, major_label_text_font_style, major_label_text_line_height, major_tick_in, major_tick_line_alpha, major_tick_line_cap, major_tick_line_color, major_tick_line_dash, major_tick_line_dash_offset, major_tick_line_join, major_tick_line_width, major_tick_out, margin, minor_tick_in, minor_tick_line_alpha, minor_tick_line_cap, minor_tick_line_color, minor_tick_line_dash, minor_tick_line_dash_offset, minor_tick_line_join, minor_tick_line_width, minor_tick_out, name, orientation, padding, scale_alpha, subscribed_events, tags, ticker, title, title_standoff, title_text_align, title_text_alpha, title_text_baseline, title_text_color, title_text_font, title_text_font_size, title_text_font_style, title_text_line_height, visible or width
